In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function
from torch.autograd import Variable
import torch.onnx
import _init_paths

import os

import easydict

import torch
import torch.utils.data
from opts import opts
from models.model import create_model, load_model, save_model
from models.data_parallel import DataParallel
from logger import Logger
from datasets.dataset_factory import get_dataset
from trains.train_factory import train_factory

In [2]:
opt = easydict.EasyDict({"K": 100,
"aggr_weight": 0.0,
"agnostic_ex": False,
"arch": "dla_34",
"aug_ddd": 0.5,
"aug_rot": 0,
"batch_size": 16,
"cat_spec_wh": False,
"center_thresh": 0.1,
"chunk_sizes": [15],
"data_dir": "/mnt/nas/data",
"dataset": "mobiltech",
"debug": 0,
"debug_dir": "/mnt/nas/centernet/exp/ctdet/mobiltech/mobiltech_dla/debug",
"debugger_theme": "white",
"demo": "/root/practice/CenterNet/images/mobiltech_test",
"dense_hp": False,
"dense_wh": False,
"dep_weight": 1,
"dim_weight": 1,
"down_ratio": 4,
"eval_oracle_dep": False,
"eval_oracle_hm": False,
"eval_oracle_hmhp": False,
"eval_oracle_hp_offset": False,
"eval_oracle_kps": False,
"eval_oracle_offset": False,
"eval_oracle_wh": False,
"exp_dir": "/mnt/nas/centernet/exp/ctdet",
"exp_id": "mobiltech_dla",
"fix_res": True,
"flip": 1.5,
"flip_test": True,
"gpus": [0],
"gpus_str": 0,
"head_conv": 256,
"heads": {'hm': 66, 'wh': 2, 'reg': 2},
"hide_data_time": False,
"hm_hp": True,
"hm_hp_weight": 1,
"hm_weight": 1,
"hp_weight": 1,
"input_h": 512,
"input_res": 512,
"input_w": 512,
"keep_res": False,
"kitti_split": "3dop",
"load_model": "/mnt/nas/centernet/exp/ctdet/mobiltech/mobiltech_dla/model_230.pth",
"lr": 0.0005,
"lr_step": [180, 210],
"master_batch_size": 15,
"mean": [[[0.40789655, 0.44719303, 0.47026116]]],
"metric": "loss",
"mse_loss": False,
"nms": False,
"no_color_aug": False,
"norm_wh": False,
"not_cuda_benchmark": False,
"not_hm_hp": False,
"not_prefetch_test": False,
"not_rand_crop": False,
"not_reg_bbox": False,
"not_reg_hp_offset": False,
"not_reg_offset": False,
"num_classes": 66,
"num_epochs": 230,
"num_iters": -1,
"num_stacks": 1,
"num_workers": 4,
"off_weight": 1,
"output_h": 128,
"output_res": 128,
"output_w": 128,
"pad": 31,
"peak_thresh": 0.2,
"print_iter": 0,
"rect_mask": False,
"reg_bbox": True,
"reg_hp_offset": True,
"reg_loss": "l1",
"reg_offset": True,
"resume": False,
"root_dir": "/mnt/nas",
"rot_weight": 1,
"rotate": 0,
"save_all": True,
"save_dir": "/mnt/nas/centernet/exp/ctdet/mobiltech/mobiltech_dla",
"scale": 0.4,
"scores_thresh": 0.1,
"seed": 317,
"shift": 0.1,
"std": [[[0.2886383, 0.27408165, 0.27809834]]],
"task": "ctdet",
"test": False,
"test_scales": [1.0],
"trainval": False,
"val_intervals": 5,
"vis_thresh": 0.3,
"wh_weight": 0.1})

In [3]:
torch.manual_seed(opt.seed)
torch.backends.cudnn.benchmark = not opt.not_cuda_benchmark and not opt.test
Dataset = get_dataset(opt.dataset, opt.task)
opt = opts().update_dataset_info_and_set_heads(opt, Dataset)
print(opt)

heads {'hm': 66, 'wh': 2, 'reg': 2}
{'K': 100, 'aggr_weight': 0.0, 'agnostic_ex': False, 'arch': 'dla_34', 'aug_ddd': 0.5, 'aug_rot': 0, 'batch_size': 16, 'cat_spec_wh': False, 'center_thresh': 0.1, 'chunk_sizes': [15], 'data_dir': '/mnt/nas/data', 'dataset': 'mobiltech', 'debug': 0, 'debug_dir': '/mnt/nas/centernet/exp/ctdet/mobiltech/mobiltech_dla/debug', 'debugger_theme': 'white', 'demo': '/root/practice/CenterNet/images/mobiltech_test', 'dense_hp': False, 'dense_wh': False, 'dep_weight': 1, 'dim_weight': 1, 'down_ratio': 4, 'eval_oracle_dep': False, 'eval_oracle_hm': False, 'eval_oracle_hmhp': False, 'eval_oracle_hp_offset': False, 'eval_oracle_kps': False, 'eval_oracle_offset': False, 'eval_oracle_wh': False, 'exp_dir': '/mnt/nas/centernet/exp/ctdet', 'exp_id': 'mobiltech_dla', 'fix_res': True, 'flip': 1.5, 'flip_test': True, 'gpus': [0], 'gpus_str': 0, 'head_conv': 256, 'heads': {'hm': 66, 'wh': 2, 'reg': 2}, 'hide_data_time': False, 'hm_hp': True, 'hm_hp_weight': 1, 'hm_weight':

In [4]:

model = create_model(opt.arch, opt.heads, opt.head_conv)
optimizer = torch.optim.Adam(model.parameters(), opt.lr)
models= load_model(model, opt.load_model)
models= model.cuda()
dummy_input = torch.randn(16,3,512,512,device='cuda')

loaded /mnt/nas/centernet/exp/ctdet/mobiltech/mobiltech_dla/model_230.pth, epoch 230


In [5]:

torch.onnx.export(models, dummy_input, "centernet.onnx", verbose=True)

(tensor([[[[ 7.6882e-01, -5.3188e-01, -1.2897e+00,  ...,  1.9720e-01,
            6.2707e-01,  7.7747e-01],
          [-1.2624e-01,  1.1839e+00,  1.7671e+00,  ...,  3.0473e-01,
            2.1495e-01, -5.2040e-01],
          [ 3.6340e-02,  1.3939e-01, -6.1641e-01,  ...,  1.3647e+00,
           -4.9599e-01, -1.0240e-01],
          ...,
          [-1.3273e+00,  1.1675e+00,  1.3175e+00,  ...,  4.2349e-01,
            1.8351e+00,  4.4741e-01],
          [ 7.4675e-02, -4.8016e-01,  1.1053e+00,  ...,  1.1937e+00,
            1.0264e+00, -6.9947e-01],
          [-1.5172e-01, -1.2500e+00, -6.8604e-01,  ...,  9.9898e-02,
           -7.4003e-01,  1.0142e+00]],

         [[-1.0720e+00, -2.9955e-02,  2.2776e+00,  ...,  1.2646e+00,
            9.5864e-01,  3.7426e-01],
          [ 9.5383e-01, -3.6452e-01,  1.0822e+00,  ..., -6.2047e-01,
           -5.8341e-02,  2.1559e-02],
          [ 3.5365e-02, -3.1243e-01,  6.9945e-02,  ...,  2.3407e+00,
           -3.5046e-02,  4.6637e-01],
          ...,
    

tensor([[[[ 7.6882e-01, -5.3188e-01, -1.2897e+00,  ...,  1.9720e-01,
            6.2707e-01,  7.7747e-01],
          [-1.2624e-01,  1.1839e+00,  1.7671e+00,  ...,  3.0473e-01,
            2.1495e-01, -5.2040e-01],
          [ 3.6340e-02,  1.3939e-01, -6.1641e-01,  ...,  1.3647e+00,
           -4.9599e-01, -1.0240e-01],
          ...,
          [-1.3273e+00,  1.1675e+00,  1.3175e+00,  ...,  4.2349e-01,
            1.8351e+00,  4.4741e-01],
          [ 7.4675e-02, -4.8016e-01,  1.1053e+00,  ...,  1.1937e+00,
            1.0264e+00, -6.9947e-01],
          [-1.5172e-01, -1.2500e+00, -6.8604e-01,  ...,  9.9898e-02,
           -7.4003e-01,  1.0142e+00]],

         [[-1.0720e+00, -2.9955e-02,  2.2776e+00,  ...,  1.2646e+00,
            9.5864e-01,  3.7426e-01],
          [ 9.5383e-01, -3.6452e-01,  1.0822e+00,  ..., -6.2047e-01,
           -5.8341e-02,  2.1559e-02],
          [ 3.5365e-02, -3.1243e-01,  6.9945e-02,  ...,  2.3407e+00,
           -3.5046e-02,  4.6637e-01],
          ...,
     

(tensor([[[[ 7.6882e-01, -5.3188e-01, -1.2897e+00,  ...,  1.9720e-01,
            6.2707e-01,  7.7747e-01],
          [-1.2624e-01,  1.1839e+00,  1.7671e+00,  ...,  3.0473e-01,
            2.1495e-01, -5.2040e-01],
          [ 3.6340e-02,  1.3939e-01, -6.1641e-01,  ...,  1.3647e+00,
           -4.9599e-01, -1.0240e-01],
          ...,
          [-1.3273e+00,  1.1675e+00,  1.3175e+00,  ...,  4.2349e-01,
            1.8351e+00,  4.4741e-01],
          [ 7.4675e-02, -4.8016e-01,  1.1053e+00,  ...,  1.1937e+00,
            1.0264e+00, -6.9947e-01],
          [-1.5172e-01, -1.2500e+00, -6.8604e-01,  ...,  9.9898e-02,
           -7.4003e-01,  1.0142e+00]],

         [[-1.0720e+00, -2.9955e-02,  2.2776e+00,  ...,  1.2646e+00,
            9.5864e-01,  3.7426e-01],
          [ 9.5383e-01, -3.6452e-01,  1.0822e+00,  ..., -6.2047e-01,
           -5.8341e-02,  2.1559e-02],
          [ 3.5365e-02, -3.1243e-01,  6.9945e-02,  ...,  2.3407e+00,
           -3.5046e-02,  4.6637e-01],
          ...,
    

tensor([[[[ 7.6882e-01, -5.3188e-01, -1.2897e+00,  ...,  1.9720e-01,
            6.2707e-01,  7.7747e-01],
          [-1.2624e-01,  1.1839e+00,  1.7671e+00,  ...,  3.0473e-01,
            2.1495e-01, -5.2040e-01],
          [ 3.6340e-02,  1.3939e-01, -6.1641e-01,  ...,  1.3647e+00,
           -4.9599e-01, -1.0240e-01],
          ...,
          [-1.3273e+00,  1.1675e+00,  1.3175e+00,  ...,  4.2349e-01,
            1.8351e+00,  4.4741e-01],
          [ 7.4675e-02, -4.8016e-01,  1.1053e+00,  ...,  1.1937e+00,
            1.0264e+00, -6.9947e-01],
          [-1.5172e-01, -1.2500e+00, -6.8604e-01,  ...,  9.9898e-02,
           -7.4003e-01,  1.0142e+00]],

         [[-1.0720e+00, -2.9955e-02,  2.2776e+00,  ...,  1.2646e+00,
            9.5864e-01,  3.7426e-01],
          [ 9.5383e-01, -3.6452e-01,  1.0822e+00,  ..., -6.2047e-01,
           -5.8341e-02,  2.1559e-02],
          [ 3.5365e-02, -3.1243e-01,  6.9945e-02,  ...,  2.3407e+00,
           -3.5046e-02,  4.6637e-01],
          ...,
     

(tensor([[[[ 7.6882e-01, -5.3188e-01, -1.2897e+00,  ...,  1.9720e-01,
            6.2707e-01,  7.7747e-01],
          [-1.2624e-01,  1.1839e+00,  1.7671e+00,  ...,  3.0473e-01,
            2.1495e-01, -5.2040e-01],
          [ 3.6340e-02,  1.3939e-01, -6.1641e-01,  ...,  1.3647e+00,
           -4.9599e-01, -1.0240e-01],
          ...,
          [-1.3273e+00,  1.1675e+00,  1.3175e+00,  ...,  4.2349e-01,
            1.8351e+00,  4.4741e-01],
          [ 7.4675e-02, -4.8016e-01,  1.1053e+00,  ...,  1.1937e+00,
            1.0264e+00, -6.9947e-01],
          [-1.5172e-01, -1.2500e+00, -6.8604e-01,  ...,  9.9898e-02,
           -7.4003e-01,  1.0142e+00]],

         [[-1.0720e+00, -2.9955e-02,  2.2776e+00,  ...,  1.2646e+00,
            9.5864e-01,  3.7426e-01],
          [ 9.5383e-01, -3.6452e-01,  1.0822e+00,  ..., -6.2047e-01,
           -5.8341e-02,  2.1559e-02],
          [ 3.5365e-02, -3.1243e-01,  6.9945e-02,  ...,  2.3407e+00,
           -3.5046e-02,  4.6637e-01],
          ...,
    

...

[tensor([[[[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0903, 0.1439],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.2883, 0.3238],
          [0.0000, 0.2234, 0.1783,  ..., 0.0000, 0.5317, 0.1536],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000]],

         [[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0962, 0.1373,  ..., 0.0498, 0.5375, 0.2229],
          ...,
          [0.3782, 0.1930, 0.3715,  ..., 0.0000, 0.0000, 0.0000],
          [0.2140, 0.2276, 0.4613,  ..., 0.2955, 0.0077, 0.0000],
          [0.0000, 0.0940, 0.0215,  ..., 0.0000, 0.0000, 0.0000]],

         [[0.9171, 0.6600, 0.8887,  ..., 1.3342, 0.6751, 0.4074],
          [1.4151, 1.2430, 1.4240,  ..., 1.1850, 0.1161, 0.0000],
          [1.2234, 0.6680, 0.3464,  ..., 

tensor([[[[0.2819, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.4748, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0531,  ..., 1.7949, 0.0000, 0.0000],
          ...,
          [0.0000, 0.1539, 0.0000,  ..., 0.0000, 0.9727, 0.0000],
          [1.7659, 1.0062, 0.0000,  ..., 0.0000, 0.0000, 2.2455],
          [1.5866, 0.4006, 0.5449,  ..., 0.1205, 0.0000, 0.0000]],

         [[0.5822, 0.0000, 0.0000,  ..., 1.5085, 1.3729, 0.0000],
          [0.0000, 0.0000, 0.5296,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0038, 0.8125,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0876, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.2950],
          [0.1514, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.5468],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.2443, 0.2441]],

         [[0.0508, 0.0000, 0.0194,  ..., 0.0000, 0.0000, 0.4979],
          [0.3202, 0.4057, 0.0000,  ..., 0.4604, 0.5204, 1.6712],
          [0.9774, 0.5261, 0.0000,  ..., 2

tensor([[[[0.0000, 0.0000, 0.2055,  ..., 0.1051, 0.0942, 0.0766],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0132, 0.0000,  ..., 0.0000, 0.0000, 0.0120],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0192, 0.0000]],

         [[0.0492, 0.0212, 0.1301,  ..., 0.1171, 0.0144, 0.0000],
          [0.2228, 0.2170, 0.0425,  ..., 0.2162, 0.0000, 0.0457],
          [0.0177, 0.0334, 0.0116,  ..., 0.0685, 0.1181, 0.0000],
          ...,
          [0.0448, 0.1298, 0.1353,  ..., 0.0000, 0.0000, 0.0000],
          [0.0450, 0.2078, 0.1303,  ..., 0.1743, 0.2222, 0.0000],
          [0.0157, 0.1689, 0.0000,  ..., 0.2724, 0.0000, 0.0000]],

         [[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0

tensor([[[[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000]],

         [[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000]],

         [[1.4378, 1.4332, 1.4466,  ..., 1.4297, 1.4373, 1.4332],
          [1.4317, 1.4340, 1.4322,  ..., 1.4333, 1.4377, 1.4415],
          [1.4268, 1.4272, 1.4372,  ..., 1

ValueError: Auto nesting doesn't know how to process an input object of type int. Accepted types: Tensors, or lists/tuples of them

In [ ]:
25
16
16
16
16
16
1
7
14
21
14
9



20
텐서
14
텐서
9
텐서
5
텐서
14
텐서
5
텐서
14
텐서
텐서
텐서
9
텐서
5
텐서
14
텐서
5
텐서
14
텐서
텐서
텐서
9
텐서
14
텐서
텐서
3
리스트
리스트
텐서
텐서
텐서
텐서
텐서
텐서
리스트
리스트
텐서
텐서
텐서
텐서
텐서
텐서
히어
4
